In [ ]:
# 1. GitHub 레포지토리 설치
!git clone https://github.com/HaeinGeek/CancerSubtypesAI.git

Cloning into 'CancerSubtypesAI'...
remote: Enumerating objects: 905, done.
remote: Counting objects: 100% (49/49), done.
remote: Compressing objects: 100% (29/29), done.
remote: Total 905 (delta 23), reused 38 (delta 20), pack-reused 856 (from 1)
Receiving objects: 100% (905/905), 83.84 MiB | 22.71 MiB/s, done.
Resolving deltas: 100% (493/493), done.
Updating files: 100% (58/58), done.
Error downloading object: data/processed/embeddings/mut_embeddings_mean_max_cls_1.zip (d6bca3f): Smudge error: Error downloading data/processed/embeddings/mut_embeddings_mean_max_cls_1.zip (d6bca3f495793afd9b1c3027571dc3daec4558e9646f43eae0e40097294bbe09): batch response: This repository is over its data quota. Account responsible for LFS bandwidth should purchase more data packs to restore access.

Errors logged to /content/CancerSubtypesAI/.git/lfs/logs/20241020T023855.215762571.log
Use `git lfs logs last` to view the log.
error: external filter 'git-lfs filter-process' failed
fatal: data/processed/emb

In [ ]:
# 2. 작업 디렉터리 이동
%cd CancerSubtypesAI

/content/CancerSubtypesAI


In [ ]:
# 3. PYTHONPATH 설정 (processing 모듈을 패키지로 인식하도록)
import sys
sys.path.append("/content/CancerSubtypesAI")

In [ ]:
# 4. data 업로드
import os
upload_dir = 'data/processed'  # 원하는 디렉토리 경로
os.makedirs(upload_dir, exist_ok=True)

In [ ]:
# 파일 업로드
from google.colab import files
uploaded = files.upload()

In [ ]:
# 업로드된 파일을 지정 디렉토리로 이동
for filename in uploaded.keys():
    file_path = os.path.join(upload_dir, filename)
    print(f'Moved {filename} to {file_path}/')

# 데이터 로딩

In [ ]:
from embedding.protbert_embedding import (
    extract_data_for_embedding,
    load_protbert,
    apply_pooling,
    extract_embeddings,
    get_existing_keys,
    process_embeddings
)


In [ ]:
from input_calculator.embedding_input import (
    EmbeddingManager,
    create_model_input,
    convert_to_serializable,
    save_model_input,
    load_model_input
)

In [ ]:
from utils.utils import(
    setup_environment,
    load_logger,
    load_full_feature_data,
    download_file
)

In [ ]:
setup_environment()
logger = load_logger()

In [ ]:
# 임베딩 계산할 데이터 로딩
mutation_train = load_full_feature_data()
mutation_test = load_full_feature_data(train=False)

In [ ]:
print(len(mutation_train), len(mutation_test))

206989 169219


In [ ]:
import pandas as pd
mutation_df = pd.concat([mutation_train, mutation_test]).drop_duplicates(subset=['gene', 'mutation_str'])
mutation_df.reset_index(drop=True, inplace=True)

In [ ]:
len(mutation_df)

363089

In [ ]:
mutation_df[:3]

gene mutation_str             type origin position mutant  mut_num  \
0  A2M           WT               WT     []       []     []        0   
1  A2M        R895R  Silent_Missense    [R]    [895]    [R]        1   
2  A2M       E1462K         Missense    [E]   [1462]    [K]        1   

   hydrophobicity_min  hydrophobicity_max  hydrophobicity_mean  ...  pI_std  \
0                 NaN                 NaN                  NaN  ...     0.0   
1                 0.0                 0.0                  0.0  ...     0.0   
2                -0.4                -0.4                 -0.4  ...     0.0   

   charge_min  charge_max  charge_mean  charge_std  status       isoform_id  \
0         NaN         NaN          NaN         0.0       0  ENSP00000323929   
1         0.0         0.0          0.0         0.0       0           P01023   
2         2.0         2.0          2.0         0.0       0           P01023   

                                              wt_seq  \
0  MGKNKLLHPSLVLLLLVLLPTDASVSGKPQYMVLVPSLLHTETTEK...   
1  MGKNKLLHPSLVLLLLVLLPTDASVSGKPQYMVLVPSLLHTETTEK...   
2  MGKNKLLHPSLVLLLLVLLPTDASVSGKPQYMVLVPSLLHTETTEK...   

                                             mut_seq  status_prot  
0                                                NaN            0  
1  MGKNKLLHPSLVLLLLVLLPTDASVSGKPQYMVLVPSLLHTETTEK...            0  
2  MGKNKLLHPSLVLLLLVLLPTDASVSGKPQYMVLVPSLLHTETTEK...            0  

[3 rows x 32 columns]

# 임베딩 계산

In [ ]:
wt_prot, mut_prot = extract_data_for_embedding(mutation_df)

print(f'전체 샘플 길이:{len(mutation_df)}',
    f'\nwt 서열 길이: {len(wt_prot)}',
    f'\n변이 서열 길이: {len(mut_prot)}'
)

전체 샘플 길이:363089 
wt 서열 길이: 6401 
변이 서열 길이: 253548


In [ ]:
# ProtBERT tokenizer & model 로딩
tokenizer, model, device = load_protbert()

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/86.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/81.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/361 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


pytorch_model.bin:   0%|          | 0.00/1.68G [00:00<?, ?B/s]

## 코드실행

In [ ]:
# 출력 파일 기본 이름 설정
wt_output_file_base = 'data/processed/embeddings/wt_embeddings_cls'
mut_output_file_base = 'data/processed/embeddings/mut_embeddings_cls'

In [ ]:
# Wild-type embeddings
logger.info("Starting processing of wild type sequences")
process_embeddings(
    wt_prot, tokenizer, model, device, wt_output_file_base,
    pooling_strategy='mean_max_cls', batch_size=32
)

In [ ]:
# Mutant embeddings
logger.info("Starting processing of mutant sequences")
process_embeddings(
    mut_prot, tokenizer, model, device, mut_output_file_base,
    is_mutant=True, pooling_strategy='mean_max_cls', batch_size=32
)

In [ ]:
# Assume you have a list of existing embedding files
existing_embedding_files = ['data/processed/embeddings/wt_embeddings_mean_max_cls_1.h5',
                            'data/processed/embeddings/wt_embeddings_mean_max_cls_add_1.h5']

# Collect existing keys
existing_keys = get_existing_keys(existing_embedding_files)

# Process embeddings, skipping existing ones
process_embeddings(
    wt_prot,
    tokenizer,
    model,
    device,
    output_file_base='data/processed/embeddings/wt_embeddings_cls_add_2',
    existing_keys=existing_keys,
    is_mutant=False,  # Set to True if processing mutant sequences
    pooling_strategy='mean_max_cls',
    batch_size=32
)


Processing batches: 0it [00:00, ?it/s]


In [ ]:
# Assume you have a list of existing embedding files
existing_embedding_files = ['data/processed/embeddings/mut_embeddings_mean_max_cls_1.h5',
                            'data/processed/embeddings/mut_embeddings_cls_add_1.h5']

# Collect existing keys
existing_keys = get_existing_keys(existing_embedding_files)

# Process embeddings, skipping existing ones
process_embeddings(
    mut_prot,
    tokenizer,
    model,
    device,
    output_file_base='data/processed/embeddings/mut_embeddings_mean_max_cls_add_2',
    existing_keys=existing_keys,
    is_mutant=True,  # Set to True if processing mutant sequences
    pooling_strategy='mean_max_cls',
    batch_size=32
)


Processing batches: 0it [00:00, ?it/s]


In [ ]:
# Assume you have a list of existing embedding files
mut_existing_embedding_files = ['data/processed/embeddings/mut_embeddings_mean_max_cls_1.h5',
                            'data/processed/embeddings/mut_embeddings_cls_add_1.h5']

# Collect existing keys
mut_existing_keys = get_existing_keys(mut_existing_embedding_files)

# Assume you have a list of existing embedding files
wt_existing_embedding_files = ['data/processed/embeddings/wt_embeddings_mean_max_cls_1.h5',
                            'data/processed/embeddings/wt_embeddings_mean_max_cls_add_1.h5']

# Collect existing keys
wt_existing_keys = get_existing_keys(wt_existing_embedding_files)

## 실행결과 확인

In [ ]:
# 생성된 임베딩 파일 확인 (WT)
import h5py
# HDF5 파일을 읽기 모드로 열기
file_path = 'data/processed/embeddings/wt_embeddings_mean_max_cls_1.h5'
with h5py.File(file_path, 'r') as f:
    # 파일의 키(데이터셋 및 그룹 이름)를 확인
    keys = list(f.keys())
    print(f"WT Dataset keys: {keys}")
    print()
    # 특정 데이터셋 읽기
    dataset = f['2QY0_2']
    print()

    # 데이터셋의 속성 정보 확인
    print(f"Shape of dataset: {dataset.shape}")
    print(f"Data type: {dataset.dtype}")
    print()

    # 데이터셋 읽기
    partial_data = dataset[:]
    print(partial_data)

WT Dataset keys: ['2QY0_2', '3BHS1_HUMAN', '5Y3R_6', '6F39_1', '8HMV_2', '8TB0_2', '8ZH8_5', 'A0A024QYR6', 'A0A024R1X5', 'A0A024R324', 'A0A024R571', 'A0A024R5Z7', 'A0A024R6A3', 'A0A024RA31', 'A0A024RCV8', 'A0A075B6Q6', 'A0A075B6R4', 'A0A075B749', 'A0A075B774', 'A0A075B788', 'A0A087WTF2', 'A0A087WTI6', 'A0A087WTR3', 'A0A087WTU9', 'A0A087WU13', 'A0A087WVP4', 'A0A087WVU1', 'A0A087WW63', 'A0A087WWD4', 'A0A087WWJ5', 'A0A087WX80', 'A0A087WX83', 'A0A087WXB8', 'A0A087WXK5', 'A0A087WY96', 'A0A087WYD6', 'A0A087WYQ1', 'A0A087WZ40', 'A0A087WZN1', 'A0A087WZR1', 'A0A087X0D5', 'A0A087X0K9', 'A0A087X1E4', 'A0A087X1N8', 'A0A087X1R1', 'A0A087X1S7', 'A0A087X1V2', 'A0A087X1Z1', 'A0A087X1Z3', 'A0A087X208', 'A0A087X2C4', 'A0A087X2D4', 'A0A087X2I1', 'A0A087X2I7', 'A0A088AWN3', 'A0A090MEW7', 'A0A090N7Y2', 'A0A090N8E9', 'A0A096LNW1', 'A0A0A0MQT0', 'A0A0A0MR13', 'A0A0A0MR42', 'A0A0A0MR51', 'A0A0A0MRF3', 'A0A0A0MRJ0', 'A0A0A0MRJ1', 'A0A0A0MRJ7', 'A0A0A0MRL7', 'A0A0A0MRM2', 'A0A0A0MRM9', 'A0A0A0MS43', 'A0A0A0MS77

In [ ]:
# 생성된 임베딩 파일 확인 (MUTANT)
file_path = 'data/processed/embeddings/mut_embeddings_mean_max_cls_1.h5'
with h5py.File(file_path, 'r') as f:
    # 파일의 키(데이터셋 및 그룹 이름)를 확인
    keys = list(f.keys())
    print(f"Mut Dataset keys: {keys}")
    print()
    # 특정 데이터셋 읽기
    # dataset = f['2QY0_2_R148W']
    dataset = f[keys[np.argmax(len_keys)]]
    print()

    # 데이터셋의 속성 정보 확인
    print(f"Shape of dataset: {dataset.shape}")
    print(f"Data type: {dataset.dtype}")
    print()

    # 데이터셋 읽기
    partial_data = dataset[:]
    print(partial_data)

Mut Dataset keys: ['2QY0_2_R148W', '3BHS1_HUMAN_A184V', '3BHS1_HUMAN_A339V', '3BHS1_HUMAN_A349S', '3BHS1_HUMAN_E110Q', '3BHS1_HUMAN_E143*', '3BHS1_HUMAN_F218L A334V', '3BHS1_HUMAN_G171R', '3BHS1_HUMAN_G216E', '3BHS1_HUMAN_G227S', '3BHS1_HUMAN_G90S', '3BHS1_HUMAN_H233Y', '3BHS1_HUMAN_H262Y', '3BHS1_HUMAN_H93N', '3BHS1_HUMAN_P223L', '3BHS1_HUMAN_P243T', '3BHS1_HUMAN_Q351K', '3BHS1_HUMAN_R312*', '3BHS1_HUMAN_R317H', '3BHS1_HUMAN_T105I E46K', '3BHS1_HUMAN_T353M', '3BHS1_HUMAN_V100I', '3BHS1_HUMAN_W284*', '3BHS1_HUMAN_W356*', '3BHS1_HUMAN_Y254*', '3BHS1_HUMAN_Y292* S359F', '3BHS1_HUMAN_Y292H', '5Y3R_6_G1547V', '5Y3R_6_Q2041*', '5Y3R_6_Q3568E', '6F39_1_E103K', '8HMV_2_G63V', '8TB0_2_T612M R374C', '8ZH8_5_A2V', 'A0A024QYR6_A126G', 'A0A024QYR6_A126V', 'A0A024QYR6_D326G', 'A0A024QYR6_G209A', 'A0A024QYR6_H93L', 'A0A024QYR6_H93R', 'A0A024QYR6_I28S', 'A0A024QYR6_L325R', 'A0A024QYR6_R74T', 'A0A024QYR6_Y88H', 'A0A024R1X5_Q19*', 'A0A024R324_A148T', 'A0A024R324_A61D', 'A0A024R324_A61V', 'A0A024R324_D5

In [ ]:
print(len(set(wt_existing_keys)), len(set(mut_existing_keys)))

6401 253548


# 인풋 데이터 계산

## 코드실행

In [ ]:
train_df = pd.read_csv('data/train.csv')
test_df = pd.read_csv('data/test.csv')

In [ ]:
embedding_dir = 'data/processed/embeddings/'

In [ ]:
# 학습 인풋 생성
train_input = create_model_input(train_df, mutation_df, embedding_dir)

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.


In [ ]:
# 모델 입력 데이터 저장
save_model_input(train_input, 'data/processed/train/input_data.json')

모델 입력 데이터가 data/processed/train/input_data.json에 저장되었습니다.


In [ ]:
download_file('/content/CancerSubtypesAI/data/processed/train/input_data.json')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

/content/CancerSubtypesAI/data/processed/train/input_data.json 파일이 다운로드되었습니다.


In [ ]:
# 테스트 인풋 생성
test_input = create_model_input(test_df, mutation_df, embedding_dir)

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.


In [ ]:
# 모델 입력 데이터 저장
save_model_input(test_input, 'data/processed/test/input_data.json')

모델 입력 데이터가 data/processed/test/input_data.json에 저장되었습니다.


In [ ]:
download_file('/content/CancerSubtypesAI/data/processed/test/input_data.json')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

/content/CancerSubtypesAI/data/processed/test/input_data.json 파일이 다운로드되었습니다.


## 실행결과 확인

In [ ]:
# 결과 확인
print("생성된 학습 입력 개수:", len(train_input))
print("\n첫 번째 학습 샘플의 구조:")
print(json.dumps(train_input[0], indent=2, default=lambda x: x.tolist() if isinstance(x, np.ndarray) else str(x)))

생성된 학습 입력 개수: 2

첫 번째 학습 샘플의 구조:
{
  "subclass": "KIPAN",
  "id": "TRAIN_0000",
  "mutation_stats": {
    "num_mutated_genes": 25,
    "mutations": {
      "K277K": 1,
      "G592G": 1,
      "A699T": 1,
      "F736C": 1,
      "A746D": 1,
      "I136M": 1,
      "N23K": 1,
      "G764G": 1,
      "V412A": 1,
      "A219T": 1,
      "L192V": 1,
      "N1445D": 1,
      "P222R": 1,
      "L111L": 1,
      "R305S": 1,
      "R104H": 1,
      "D623D": 1,
      "D465D": 1,
      "P117R": 1,
      "E237*": 1,
      "T218T": 1,
      "I382M": 1,
      "P17R": 1,
      "E291A": 1,
      "E660Q": 1
    },
    "mutation_type_freq": {
      "Silent_Missense": 7,
      "Nonsense": 1,
      "Missense": 17
    }
  },
  "aa_change_stats": {
    "hydrophobicity": {
      "hydrophobicity_min": -0.6916666666666665,
      "hydrophobicity_max": -0.6916666666666665,
      "hydrophobicity_mean": -0.6916666666666665,
      "hydrophobicity_std": 0.0
    },
    "polarity": {
      "polarity_min": 0.2083333333

In [ ]:
print("생성된 테스트 입력 개수:", len(test_input))
print("\n첫 번째 테스트 샘플의 구조:")
print(json.dumps(test_input[0], indent=2, default=lambda x: x.tolist() if isinstance(x, np.ndarray) else str(x)))

print("\첫 번째 학습 샘플의 mutation_stats:")
print(json.dumps(test_input[0]['mutation_stats'], indent=2))

생성된 테스트 입력 개수: 2546

첫 번째 테스트 샘플의 구조:
{
  "id": "TEST_0000",
  "mutation_stats": {
    "num_mutated_genes": 52,
    "mutations": {
      "D163E D152E": 1,
      "S55S": 1,
      "S316P": 1,
      "T262R": 1,
      "R116H": 1,
      "G5E": 1,
      "T24P": 1,
      "S126X": 1,
      "P26H": 1,
      "S221Kfs S205Kfs S262Kfs S169Kfs": 1,
      "Y229Y Y271Y": 1,
      "M267I M206I": 1,
      "T446T": 1,
      "N120T": 1,
      "I345I": 1,
      "T601M T598M": 1,
      "Q2870Q": 1,
      "F540L": 1,
      "P233del": 1,
      "S1319S": 1,
      "Y1289H": 1,
      "Y204X Y226X Y222X Y200X Y168X Y199X Y202X Y221X Y224X Y169X Y241X Y197X Y171X Y207X Y166X": 1,
      "V18G": 1,
      "T102A": 1,
      "V69V": 1,
      "K70R": 1,
      "R123H": 1,
      "M123I": 1,
      "P634P": 1,
      "R472R R492R R429R": 1,
      "V2194V V1030V": 1,
      "F119L": 1,
      "R493C": 1,
      "S293S": 1,
      "A166A": 1,
      "Q117R K392E K324E K303E K662E K456E K705E": 1,
      "G104C G103C": 1,
      "R43

In [ ]:
# embedding_stats가 None인 샘플 수 확인
none_count_train = sum(1 for sample in train_input if sample['embedding_stats'] is None)
none_count_test = sum(1 for sample in test_input if sample['embedding_stats'] is None)
print(f"전체 샘플 수: {len(train_df)}")
print(f"\nembedding_stats가 None인 샘플 수: {none_count_train + none_count_test}")

# status_prot가 1인 mutation의 수 확인
status_prot_1_count = mutation_df[mutation_df['status_prot'] == 1].shape[0]
print(f"\nstatus_prot가 1인 mutation의 수: {status_prot_1_count}")

전체 샘플 수: 6201

embedding_stats가 None인 샘플 수: 167

status_prot가 1인 mutation의 수: 36888
